In [13]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
import time
import random
import pandas as pd
import re

In [14]:
# 데이터 불러오기 & text 컬럼 추가
data=pd.read_excel('./tour_100_list.xlsx')
data['text']=''
data

관광지                              주소 text
0        경복궁          서울특별시 종로구 사직로 161(경복궁)     
1        창덕궁           서울특별시 종로구 율곡로 99(창덕궁)     
2        창경궁         서울특별시 종로구 창경궁로 185(창경궁)     
3        덕수궁          서울특별시 종로구 세종대로 99(덕수궁)     
4        경희궁          서울특별시 종로구 새문안로 55(경희궁)     
..       ...                             ...  ...
117  한라산국립공원   제주특별자치도 제주시 제주시 1100로 2070-61     
118    제주올레길               제주특별자치도 제주시, 서귀포시     
119       우도            제주특별자치도 제주시 삼양고수물길 1     
120      비자림        제주특별자치도  제주시 구좌읍 비자숲길 55     
121  제주돌문화공원        제주특별자치도 제주시 조천읍 남조로 2023     

[122 rows x 3 columns]

In [15]:
# 파이썬으로 크롬 접근 
from selenium import webdriver

# 크롬창 열기
driver=webdriver.Chrome()

# 블로그 검색
driver.get('https://search.naver.com/search.naver?query=&nso=&where=blog&sm=tab_opt')
driver.implicitly_wait(10) 
time.sleep(3+random.random()*2)

In [16]:
texts=[]
for n in data['관광지']:
    
    # 검색
    search=driver.find_element(By.CLASS_NAME, 'box_window')
    search.clear()  # 검색창 지우고
    search.send_keys(n) # 검색어 입력
    time.sleep(1+random.random()*2)
    search.send_keys(Keys.RETURN) # enter 키
    
    # 페이지 스크롤
    for _ in range(30):
        driver.execute_script("window.scrollBy(0, 3000)")
        time.sleep(random.random()*2)
    
    # 제목 + 첫 문단 텍스트만 크롤링
    text = driver.find_element(By.CLASS_NAME, 'sc_new.sp_nblog._au_view_tab._svp_list').text
    # 불용어 제외
    text = text.replace('\n','').replace('블로그','').replace('문서','').replace('저장하기','').replace(n,'')
    
    # 리스트에 저장
    texts.append(text)

In [17]:
data['text'] = texts
data

관광지                              주소  \
0        경복궁          서울특별시 종로구 사직로 161(경복궁)   
1        창덕궁           서울특별시 종로구 율곡로 99(창덕궁)   
2        창경궁         서울특별시 종로구 창경궁로 185(창경궁)   
3        덕수궁          서울특별시 종로구 세종대로 99(덕수궁)   
4        경희궁          서울특별시 종로구 새문안로 55(경희궁)   
..       ...                             ...   
117  한라산국립공원   제주특별자치도 제주시 제주시 1100로 2070-61   
118    제주올레길               제주특별자치도 제주시, 서귀포시   
119       우도            제주특별자치도 제주시 삼양고수물길 1   
120      비자림        제주특별자치도  제주시 구좌읍 비자숲길 55   
121  제주돌문화공원        제주특별자치도 제주시 조천읍 남조로 2023   

                                                  text  
0     2023.09.17.은우맘의 취미생활광화문 역 맛집 엄마와 한정식 점심 꽃누리들밥...  
1     2023.10.07.동에번쩍 서에번쩍 구길동 trip서울궁투어  후원 예약방법 전...  
2     2023.10.06.사나의 여행 대온실 서울 궁궐 데이트, 주차장 정보까지 대온실...  
3     3일 전allegro con brio서울 한정식 맛집 한가람 본점 시청  점심서울...  
4     2023.01.22.장돌뱅이와 곱단이의 살아가는 이야기정조는 「지(慶熙宮誌)」에 ...  
..                                                 ...  
117   2022.03.11.기억창고 :)(어리목-남벽-영실)-어리목탐방안내소 한라산을 다...  
118   2023.10.01.당신의 일상은 안녕한가요?서귀포 여행 제주 가파도 배시간 제주...  
119   어제박로우 : 천천히 걸어가기횟집 회양과국수군 직접 잡아 손질하는 제주도 물회 맛...  
120   3일 전모든 일이 일어나는 데는 이유가 있어요푸르른 천년의 숲  (Feat. 그린...  
121   2023.10.01.곱딱하게 제주를 여행하는 방법제주 돌문화공원 입장료 주차장 전...  

[122 rows x 3 columns]

In [18]:
# 한글과 띄어쓰기만 남기기 -> 정규식
kr_texts = [re.sub(r'[^가-힣\s]', '', text) for text in texts]
kr_texts

[' 은우맘의 취미생활광화문 역 맛집 엄마와 한정식 점심 꽃누리들밥 점오랜만에 역 근처에서 약속을 잡았어요 양식을 좋아하지 않으시기 때문에 한정식 점심을 먹으려고 광화문 역 맛집 꽃누리들밥 점으로 예약을 잡았답니다 예약을 잡았지만 엄마와 전 가장 첫 타임에 방문하기로 했어요 꽃누리들밥은 역과 안국역 시간 전멜로디의 여행의 모든것 월대 복원 광화문 현판 교체 사진찍기 좋은 곳의 월대 복원 공사가 마무리되었고 광화문의 현판도 교체가 되었다고 해요 실제 방문해서 담은 여러 가지 모습과 그와 관련된 이야기도 같이 해보도록 할게요 추가로 사진 찍기 좋은 곳도 하나 소개 드릴게요 주소  서울 종로구 사직로  운영시간     세렝게티서울 서촌  데이트 코스 이탈리안 레스토랑 한옥달내돈내산 한옥 달  영업시간     일요일 휴무  주소  서울 종로구 자하문로가길   전화   주말에 에 가기로 정하고 전날 예약한 서촌 한옥 레스토랑 한옥 달 캐치테이블에서 인근 식당을 찾던 중 한옥 뷰도 이쁘고 음식도 몽몽의 먹어야 사는  고기집 서촌 뜰애우곱창타운 소곱창 데이트 고기집 서촌 뜰애우곱창타운 소곱창 데이트 안녕하세요 몽몽이에요 지난주에 친한 친구들하고 서울에 있는 식당들 탐방을  고기집 위치는 지하철역 바로 앞입니다 여기가 세종마을 음식문화거리인데 여기에서도 유명한 식당이에요 주소  서울특별시 종로구 일 전여행쟁이 우수서울 가볼만한곳  생과방 예약 궁중문화축전 월 국내서울 가볼만한곳  생과방 예약 궁중문화축전 월 국내 축제 글사진 우수 작년에 처음 궁중문화축전이라는 걸 알게 됐는데 은 언제 가도 좋지만 일년에 한번 있는 축제때 가면 더 좋겠다는 생각이 들더라구요  작년 축제 첫날에 바로 다녀왔는데 올해는 조금 늦은 시간 전무한긍정소녀 행복한  삼청동 카페  테라로사 국립현대미술관서울점 삼청동 근처에 있는 카페 중 조용하고 분위기 좋은 카페 아닐까 생각해봅니다 저는 오픈런으로 국립현대미술관 전시를 다 보고 보이는  삼청동 카페 답지요 옆쪽은 이런 공간  한켠에는 혼자 앉아서 커피를

In [19]:
data['kr_text']=kr_texts
data

관광지                              주소  \
0        경복궁          서울특별시 종로구 사직로 161(경복궁)   
1        창덕궁           서울특별시 종로구 율곡로 99(창덕궁)   
2        창경궁         서울특별시 종로구 창경궁로 185(창경궁)   
3        덕수궁          서울특별시 종로구 세종대로 99(덕수궁)   
4        경희궁          서울특별시 종로구 새문안로 55(경희궁)   
..       ...                             ...   
117  한라산국립공원   제주특별자치도 제주시 제주시 1100로 2070-61   
118    제주올레길               제주특별자치도 제주시, 서귀포시   
119       우도            제주특별자치도 제주시 삼양고수물길 1   
120      비자림        제주특별자치도  제주시 구좌읍 비자숲길 55   
121  제주돌문화공원        제주특별자치도 제주시 조천읍 남조로 2023   

                                                  text  \
0     2023.09.17.은우맘의 취미생활광화문 역 맛집 엄마와 한정식 점심 꽃누리들밥...   
1     2023.10.07.동에번쩍 서에번쩍 구길동 trip서울궁투어  후원 예약방법 전...   
2     2023.10.06.사나의 여행 대온실 서울 궁궐 데이트, 주차장 정보까지 대온실...   
3     3일 전allegro con brio서울 한정식 맛집 한가람 본점 시청  점심서울...   
4     2023.01.22.장돌뱅이와 곱단이의 살아가는 이야기정조는 「지(慶熙宮誌)」에 ...   
..                                                 ...   
117   2022.03.11.기억창고 :)(어리목-남벽-영실)-어리목탐방안내소 한라산을 다...   
118   2023.10.01.당신의 일상은 안녕한가요?서귀포 여행 제주 가파도 배시간 제주...   
119   어제박로우 : 천천히 걸어가기횟집 회양과국수군 직접 잡아 손질하는 제주도 물회 맛...   
120   3일 전모든 일이 일어나는 데는 이유가 있어요푸르른 천년의 숲  (Feat. 그린...   
121   2023.10.01.곱딱하게 제주를 여행하는 방법제주 돌문화공원 입장료 주차장 전...   

                                               kr_text  
0     은우맘의 취미생활광화문 역 맛집 엄마와 한정식 점심 꽃누리들밥 점오랜만에 역 근처...  
1     동에번쩍 서에번쩍 구길동 서울궁투어  후원 예약방법 전각 입장료 주차장꿀팁내돈내산...  
2     사나의 여행 대온실 서울 궁궐 데이트 주차장 정보까지 대온실 생각이 딱 나더라고요...  
3     일 전  서울 한정식 맛집 한가람 본점 시청  점심서울 한정식 맛집 시청  점심 ...  
4     장돌뱅이와 곱단이의 살아가는 이야기정조는 지에 이렇게 썼다 대체로 궁궐이란 임금이...  
..                                                 ...  
117   기억창고 어리목남벽영실어리목탐방안내소 한라산을 다시는 안 올줄 알았다 재미 없는 ...  
118   당신의 일상은 안녕한가요서귀포 여행 제주 가파도 배시간 제주 올레길 코스 추천제주...  
119   어제박로우  천천히 걸어가기횟집 회양과국수군 직접 잡아 손질하는 제주도 물회 맛집...  
120   일 전모든 일이 일어나는 데는 이유가 있어요푸르른 천년의 숲   그린카드  무료입...  
121   곱딱하게 제주를 여행하는 방법제주 돌문화공원 입장료 주차장 전기차 셔틀버스 이용후...  

[122 rows x 4 columns]

In [20]:
# csv파일로 저장
data.to_csv('crawling_data_.csv', encoding='utf-8')